In [ ]:
# Reading in, manipulations
import numpy as np
import pandas as pd

# Plotting
import plotly_express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Clustering
from sklearn.preprocessing import PowerTransformer
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA

import warnings
warnings.filterwarnings(action = "ignore")

Setting my color scheme

In [ ]:
custom_color_scale = ['#0000FF', '#33CCFF', '#66FF99', '#D2D200', '#FFFF00']

Reading data

In [ ]:
df = pd.read_csv("data/cc_general.csv")

#### EDA

Making columns lowercase

In [ ]:
df.columns = df.columns.str.lower()

Checking for NAs

In [ ]:
df.isnull().sum().sort_values(ascending = False)

We've got some missing values, will deal with them later. Let's check the distributions ...

In [ ]:
df.describe()

There are quite some outliers!

In [ ]:
df.drop(['cust_id'], axis = 1, inplace = True)

Removing the customer Id as we will not need it.

In [ ]:
fig = px.box(df)
fig.update_layout(
    title_text = 'Not only quite some outliers but the range across variables is different.'
)
fig.show()

We will need to standardize the data later for clustering.

In [ ]:
nr_columns = len(df.columns)
nr_rows = (nr_columns + 1) // 2
nr_cols = 2

fig = make_subplots(rows = nr_rows, cols = nr_cols, subplot_titles = df.columns)

for i, col in enumerate(df.columns):
    row_num = (i // nr_cols) + 1 
    col_num = (i % nr_cols) + 1   
    fig.add_trace(go.Histogram(x = df[col], nbinsx = 30, name = str(col)), row = row_num, col = col_num)

fig.update_layout(height = 900, width = 600, showlegend = False)
fig.update_xaxes(tickfont = dict(size = 8))
fig.update_yaxes(tickfont = dict(size = 8))

fig.show()

In [ ]:
df[df['purchases'] == 0] 

* We've got customers that had no purchases, however their balance did go down due to cash advances. Could also because of fees or interest rates.
* Also, the balance does not seem to match up if we add together payments and cash advances so it could be that the balance considers the previous billing cycle.

OK, let's start by looking at the most important variable when it comes to credit cards and that is their limit.

In [ ]:
px.histogram(df, x = 'credit_limit', nbins = 100)

As expected, most limits are low.

In [ ]:
px.scatter(df, x = 'credit_limit', y = 'payments')

So we can see ...
* we've got a variety of purchase behaviors and ...
* higher credit limit does not presume higher payment amounts.

In [ ]:
px.scatter(df, x = 'purchases', y = 'payments', color = 'cash_advance', trendline = 'ols')

* But the more purchases the more likely the payments are high.  
* As noticed before, we can see quite some customers not making purchases, partly becaus of cash advances and the other part cannot be explained from this dataset.

It's still a bit fuzzy, let's move on to correlations ...

In [ ]:
correlation_matrix = df.corr()
fig = go.Figure(
    data = go.Heatmap(
            x = correlation_matrix.columns,
            y = correlation_matrix.index,
            z = correlation_matrix.values,
            colorscale = 'YlGnBu')
)

fig.show()

Things that impact each other, of course are highly correlated as ...
* ... credit limit and balance
* ... purchases frequency and one-off purchases frequency
* ... purchases and installments purchases
* ... etc.

That means, quite some variables probably will not be needed to cluster our customers.

For really understanding where the most variation comes from I will use PCA.
But before that, our features need some pre-processing!

#### Pre-processing
1. Inputting missing values - we have a right-skewed distribution, so will use the median to impute the missing numbers.
2. Dropping the one row that has a missing value in credit limit.


In [ ]:
px.histogram(df, x = 'minimum_payments', nbins = 50)

In [ ]:
df.dropna(subset = ['credit_limit'], inplace = True)
df['minimum_payments'].fillna(df['minimum_payments'].median(), inplace = True)
print(df.isnull().sum())

As we have observed, most variables are skewed, so we need to ...
1. Normalize the variables with PowerTransformer
2. Store it separately for clustering

P.S Using PowerTransformer for (1) since we have a variation of different distributions (right skewed, negatively skewed and bimodal) and 
the features have significantly different scales and variances.

In [ ]:
from sklearn.preprocessing import PowerTransformer
scaler = PowerTransformer()
X = scaler.fit_transform(df)
np.allclose(np.mean(X), 0)
np.allclose(np.std(X), 1)

Superfluous step but just so the user know that the data is clearly normalized. Finally, it's time for PCA!

#### PCA
1. Use all variables
2. Check the highest variance explained
3. Plot loadings

In [ ]:
pca = PCA(n_components = None)
X_pca = pca.fit_transform(X)
X_pca_df = pd.DataFrame(X_pca, columns = df.columns)
print(X_pca_df)

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x = list(range(1, len(pca.explained_variance_) + 1)),
    y = pca.explained_variance_,
    marker = dict(color = 'blue')
))

fig.update_layout(
    title = "The bend occurs at eigenvalue number 3.",
    xaxis = dict(title = "Eigenvalue number"),
    yaxis = dict(title = "Eigenvalue size"),
)

fig.show()

It could be a signal that using the first 3 components could be enough.
Let's look at the explained variance.

In [ ]:
exp_var_cumul = np.cumsum(pca.explained_variance_ratio_)

px.area(
    x = range(1, exp_var_cumul.shape[0] + 1),
    y = exp_var_cumul,
    labels = {"x": "# Components", "y": "Explained Variance"}
)

It's around 5 components where we keep 80% of the explained variance.

In [ ]:
features = df.columns
loadings = pca.components_.T * np.sqrt(pca.explained_variance_)

fig = px.scatter(X_pca, x = 0, y = 1)

for i, feature in enumerate(features):
    fig.add_annotation(
        ax = 0, ay = 0,
        axref="x", ayref="y",
        x = loadings[i, 0],
        y = loadings[i, 1],
        arrowsize = 0.5,
        arrowhead = 1,
        xanchor = "right",
        yanchor = "top")

    fig.add_annotation(
        x=loadings[i, 0],
        y=loadings[i, 1],
        ax=0, ay=0,
            text = f"{feature} (PC1): {loadings[i, 1]:.2f} and (PC2): {loadings[i, 0]:.2f}",

        yshift=-15
    )

# Show the plot
fig.show()

* We can notice one clear cluster on the left side separate from the big cluster.
* The features that contribute the most to PC1 are the balance and minimum payments, whereas, for PC2 (the y-axis), the largest contributors are a mix from purchases, installments and cash advances.
* Variables that close together such as puchases & purchases_trx or oneoff_purchases_frequency and oneoff_purchases are positively correlated.

We can notice one clear cluster on the left side separate from the big cluster.

Will use 3 PCA components as features for the Kmeans, as it explains enough of the variance and does not add too much complexity.

In [ ]:
pca = PCA(n_components = 3)
X_pca = pca.fit_transform(X)

#### K-Means

In [ ]:
kmeans_models = [KMeans(n_clusters = k, random_state = 1, verbose = False).fit(X_pca) for k in range (1, 10)]
inertia = [model.inertia_ for model in kmeans_models]

fig = go.Figure()
fig.add_trace(go.Scatter(
              x = list(range(1, 12)), 
              y = inertia, 
              mode = 'lines+markers', 
              marker = dict(size = 10), line = dict(color = 'blue'))
              )
fig.update_layout(title = 'The elbow is around 5 clusters.',
                  xaxis = dict(title = 'Number of Clusters'),
                  yaxis = dict(title = 'WCSS'))

fig.show()

The intertia drop is minimal after K = 5, therefore 5 would be considered as an optimal number of clusters.

In [ ]:
from sklearn.metrics import silhouette_score

silhouette_scores = [silhouette_score(X_pca, model.labels_) for model in kmeans_models[1:5]]
for k, score in enumerate(silhouette_scores, start = 2):
    print(f"Number of clusters: {k}")
    print(f"Silhouette score: round{score}")
    print()

Will move on with 5 clusters. Let's see how it looks like.

In [ ]:
kmeans = KMeans(n_clusters = 5, random_state = 23)
kmeans.fit(X_pca)

Adding the clusters into the dataframe ...

In [264]:
df_pca_kmeans = pd.concat([df.reset_index(drop = True), pd.DataFrame(X_pca)], axis = 1)
df_pca_kmeans.columns.values[-3: ] = ['PC_1', 'PC_2', 'PC_3']
df_pca_kmeans = df_pca_kmeans.reset_index(drop = True)
df_pca_kmeans['cluster_id'] = kmeans.labels_
cluster_names = {0: 1, 1: 2, 2: 3, 3: 4, 4: 5}
df_pca_kmeans['cluster'] = df_pca_kmeans['cluster_id'].map(cluster_names)

In [258]:
x_axis = df_pca_kmeans['PC_1']
y_axis = df_pca_kmeans['PC_2']
px.scatter(x = x_axis, y = y_axis, color = df_pca_kmeans['cluster'], color_continuous_scale = custom_color_scale)

The model is not perfect, but unfortunately the points do not create super clear clusters, as there is quite some variance.

Introducing the third component ...

In [260]:
z_axis = df_pca_kmeans['PC_3']
px.scatter_3d(x = x_axis, y = y_axis, z = z_axis, color = df_pca_kmeans['cluster'], color_continuous_scale = custom_color_scale)

Now, let's go back to the original data and see what that actually means.

In [267]:
fig = px.box(df_pca_kmeans, x = 'cluster', y = 'credit_limit')
fig.update_layout(
    title_text = 'Credit limit is higher for cluster 1 and 2.'
)

We can see that the first two clusters are the ones with higher limit. Would assume they also spend more?

In [269]:

fig = px.scatter(df_pca_kmeans, x = 'credit_limit', y = 'purchases', color = 'cluster', color_continuous_scale = custom_color_scale)
fig.update_layout(
    title_text = 'Cluster 4 and 5 are not big purchasers.'
)

Yes, that is definitely one additional differentiator. The lower part contain customers that do not make a lot of purchases - cluster 4, 5.

In [271]:
fig = px.scatter(df_pca_kmeans, x = 'credit_limit', y = 'balance', color = 'cluster',  color_continuous_scale = custom_color_scale)
fig.update_layout(
    title_text = '... especially Cluster 4 of customers does not use it for much.'
)

Now we can see that last two clusters (4, 5) are customers that do not make much business. But for the rest, this is not a clear differentiator.  
Where does it come from then? Let's check cash advances, as we have seen in the past that there were quite some.

In [272]:
fig = px.box(df_pca_kmeans, x = 'cluster', y = 'cash_advance', log_y = True)
fig.update_layout(
    title_text = '... Cash advances are a favourite for cluster 1 and 3.'
)

Here is where cluster 3 comes in. These are the customers who have an ok limit but they use it for quite some cash advances.

Let's go back to our PCA view, and observe the impact by certain variables.

In [273]:
x_axis = df_pca_kmeans['PC_1']
y_axis = df_pca_kmeans['PC_2']
px.scatter(x = x_axis, y = y_axis, color = df_pca_kmeans['credit_limit'], color_continuous_scale = custom_color_scale)

Now, if we remember our clusters. We can already see that the lower part is mostly low credit limit and higher part of y axis is higher limit.   
But, still, this explains a small part of it.

This variable seems to cluster the lower cluster, the 5th - the low limit customers that do not really make business.

In [274]:
px.scatter(x = x_axis, y = y_axis, color = df_pca_kmeans['purchases_frequency'], color_continuous_scale = custom_color_scale)

Now we are getting somewhere. 
* You see how the cluster on the left side is clearly far away from all? This is the no or almost no usage group.
* Then on the other side we've got the high purchase group.


In [275]:
df_cluster_metrics = df_pca_kmeans.groupby('cluster').describe().T.reset_index().rename(columns = {'level_0': 'Column', 'level_1': 'Metrics'})

In [276]:
df_cluster_profile = df_cluster_metrics[df_cluster_metrics['Metrics'] == '50%'].set_index('Column').reset_index()
df_cluster_profile.style.background_gradient(cmap = 'YlGnBu', axis = 1).hide_index()

* Cluster 1 (Active Cash Advance Customers)
They have a high limit than most and they use it for purchasing stuff. Additionally, they make use of installments and a bit of cash advances.

* Cluster 2 (All-in Active Customers)
They have a higher limit than Cluster 1, however they purchase even more frequently and have a higher use of installments.

* Cluster 3 (Cash Advance Customers)
They have a lower limit and use a higher proportion of it for cash advances than others.

* Cluster 4 (Dead Customers)
They do no do much. They do not buy, they do not take cash advances.

* Cluster 5 (Installment Customers)
They prefer safety and therefore to make purchases via installments, and do not take any cash advance.

So what kind of marketing could the bank target depending on the customer?

#### Marketing Strategies

**Cluster 1 (Active Cash Advance Customers):**

* How: Provide discounts or rewards for specific purchase categories.
* Why: Maintain the interest.

**Cluster 2 (All-in Active Customers):**
* How: Introduce exclusive rewards for high-frequency transactions.
* Why: This group has the money and like to spend it.

**Cluster 3 (Cash Advance Customers):**
* How: Explore other credit card types e.g. low cash advance but low fees and higher tenure.
* Why: Too frequent cash advances are risky for a bank. In the best case, this group of customers would decrease in size and move to the Active Customer group.

**Cluster 4 (Dead Customers):**
* How: Consider contacting customers with surveys to understand their disengagement reasons.
* Why: This group would need to be understood first before targeting with a marketing technique.
Why don't they purchase? Are these people with lower income, are they young?


**Cluster 5 (Installment Customers):**
* How: Develop partnerships with merchants offering installment-friendly services and potentially that are low in interest.
* Why: It is scalable across other clusters e.g. dead customers. 